# Imports

In [3]:
from gensim.test.utils import common_texts, get_tmpfile
from gensim.models import Word2Vec
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.neural_network import MLPClassifier
from sklearn import datasets, svm, tree, metrics
from sklearn.cluster import KMeans
from sklearn import preprocessing
import matplotlib.pyplot as plt
from pandas import DataFrame
from pathlib import Path
import collections
import numpy as np
import subprocess
import itertools
import os.path
import random
import time
import json
import sys
import re
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from nltk.tokenize import word_tokenize
import nltk

# Load Data

In [4]:
with open('input_data.json') as data:
    jdata = json.load(data)

# Clean the Data

In [5]:
def codeToList(code):
    clean_string = ' '.join(code.split())
    the_list = re.split(' |\r\n',clean_string)
    return the_list





#  Function to Translate Operators to Natural Langauge 

In [39]:
def naive_word_conversion(code_string):
    
    code_string = re.sub('\>\>=', ' is reassigned after shifting right by ', code_string)
    code_string = re.sub('\<\<=', ' is reassigned after shifting left by ', code_string)
    code_string = re.sub('\<\<', ' is shifted left by ', code_string)
    code_string = re.sub('\>\>', ' is shifted right by ' , code_string)
    code_string = re.sub('\<=', ' is less than or equal to ', code_string)
    code_string = re.sub('\>=', ' is greater than or equal to ', code_string)
    code_string = re.sub('-\>', ' is dereferenced and retrieves ', code_string)
    code_string = re.sub('\<', ' is less than ', code_string)
    code_string = re.sub('\>', ' is greater than ', code_string)
    code_string = re.sub('\+\+' ,' is incremented by one ' , code_string)
    code_string = re.sub('--', ' is decremented by one ', code_string)
    code_string = re.sub('\+=', ' is reassinged after adding ' , code_string)
    code_string = re.sub('\-=', ' is reassigned after subtracting ', code_string)
    code_string = re.sub('\*=', ' is reassigned after multiplying by ', code_string)
    code_string = re.sub('\/=', ' is reassigned after dividing by ', code_string)
    code_string = re.sub('\%=', ' is reassigned after moding by ', code_string)
    code_string = re.sub('&=', ' is reassigned after a bitwise AND of ', code_string)
    code_string = re.sub('\|=', ' is reassigned after a bitwise inclusive OR of ', code_string)
    code_string = re.sub('\^=', ' is reassigned after a bitwise exclusive OR of ', code_string)
    code_string = re.sub('==', ' is equal to ', code_string)
    code_string = re.sub('\!=', ' is not equal to ', code_string)
    code_string = re.sub('&&', ' and ', code_string)
    code_string = re.sub('\|\|', ' or ', code_string)
    code_string = re.sub('\?', ' is true then ', code_string)
    code_string = re.sub('\:', ' else is false then ', code_string)
    code_string = re.sub('\/\/', '  ', code_string)
    code_string = re.sub('=', ' equals ', code_string)
    code_string = re.sub('\.', ' uses ', code_string)
    code_string = re.sub(' -{1} ', ' is subtracted from ', code_string)
    code_string = re.sub('\+{1}', ' is added to ', code_string)
    code_string = re.sub('\/\*([^\*]|(\*+([^\*\/])))*\*\/', ' ', code_string)  
    code_string = re.sub('\*{1}', ' is multiplied by ', code_string)
    code_string = re.sub('&{1}', ' has an AND done with ', code_string)
    code_string = re.sub('\/{1}', ' is divided by ', code_string)
    code_string = re.sub('\%{1}', ' is moded by ', code_string)
    code_string = re.sub('\!{1}', ' is negated ', code_string)
    code_string = re.sub('\|{1}', ' has an OR done with ', code_string)
    code_string = re.sub('\^{1}', ' has an X OR done with ', code_string)
    code_string = re.sub('\(', ' open parenthesis ', code_string)
    code_string = re.sub('\)', ' close parenthesis ', code_string)
    code_string = re.sub('\[', ' open bracket ', code_string)
    code_string = re.sub('\]', ' close bracket ', code_string)
    code_string = re.sub('\#', ' ', code_string)
    code_string = re.sub(';', ' . ', code_string)
    
    return code_string

# Extract the Vectors 

In [41]:
samples = []
labels = []
index = []
for problem in jdata:
    for submissions in problem['Submissions']:
        for submission in submissions:
            code = submissions[submission]['Code'][0]
            code = naive_word_conversion(code)
            
            samples.append( codeToList(code))
            labels.append(str(problem['contestId']) + problem['index'])
            
            index.append(submission)

print(samples[0:10])

[['include', 'is', 'less', 'than', 'stdio', 'uses', 'h', 'is', 'greater', 'than', 'include', 'is', 'less', 'than', 'string', 'uses', 'h', 'is', 'greater', 'than', 'int', 'len', '.', 'char', 'data', 'open', 'bracket', '200', 'close', 'bracket', '.', 'int', 'main', 'open', 'parenthesis', 'close', 'parenthesis', '{', 'int', 'i,', 'cnt', 'equals', '0', '.', 'scanf', 'open', 'parenthesis', '"', 'is', 'moded', 'by', 's",', 'data', 'close', 'parenthesis', '.', 'len', 'equals', 'strlen', 'open', 'parenthesis', 'data', 'close', 'parenthesis', '.', 'for', 'open', 'parenthesis', 'i', 'equals', '0', '.', 'i', 'is', 'less', 'than', 'len', '.', 'i', 'is', 'incremented', 'by', 'one', 'close', 'parenthesis', '{', 'if', 'open', 'parenthesis', 'data', 'open', 'bracket', 'i', 'close', 'bracket', 'is', 'equal', 'to', "'o'", 'close', 'parenthesis', 'cnt', 'is', 'incremented', 'by', 'one', '.', '}', 'if', 'open', 'parenthesis', 'cnt', 'is', 'equal', 'to', '0', 'close', 'parenthesis', 'printf', 'open', 'pare

In [33]:
print(np.unique(labels))
len(np.unique(labels))

['926A' '926C' '926G' '931A' '931B' '932A' '932B' '934A' '934B' '935A'
 '935B' '935C' '937A' '937B' '938A' '938B' '939A' '939B' '940A' '940B'
 '940C' '946A' '946B' '946C' '948A' '950A' '950B' '952A' '952C' '954A'
 '954B' '955A' '957A' '959A' '960A' '961A' '961B' '962A' '962B' '964A'
 '965A' '967A' '975B' '976A' '976B' '977A' '977B' '978A' '978B' '978C'
 '979A' '980A']


52

# Train the NLP Model

In [42]:
%%time
max_epochs = 100
vec_size = 300
alpha = 0.025

model = Doc2Vec(vector_size  = vec_size, alpha = alpha, min_alpha = 0.00025, min_count = 1,dm = 1)


CPU times: user 1.57 ms, sys: 40 µs, total: 1.61 ms
Wall time: 1.62 ms


In [38]:
tag_labels=[[str(_d)] for i, _d in enumerate(labels)]

In [43]:
samplesSingleList = []
for eachList in samples: 
    str1 = ' '.join(eachList)
    samplesSingleList.append(str1)

tagged_data = [TaggedDocument(words=word_tokenize(_d.lower()), tags=[str(i)]) for i, _d in enumerate(samplesSingleList)]

# building the vocabulary 
model.build_vocab(tagged_data)

In [44]:
for epoch in range(max_epochs):
    model.train(tagged_data,total_examples = model.corpus_count,epochs = model.epochs)

In [45]:
[[str(i)] for i, _d in enumerate(samplesSingleList)]

[['0'],
 ['1'],
 ['2'],
 ['3'],
 ['4'],
 ['5'],
 ['6'],
 ['7'],
 ['8'],
 ['9'],
 ['10'],
 ['11'],
 ['12'],
 ['13'],
 ['14'],
 ['15'],
 ['16'],
 ['17'],
 ['18'],
 ['19'],
 ['20'],
 ['21'],
 ['22'],
 ['23'],
 ['24'],
 ['25'],
 ['26'],
 ['27'],
 ['28'],
 ['29'],
 ['30'],
 ['31'],
 ['32'],
 ['33'],
 ['34'],
 ['35'],
 ['36'],
 ['37'],
 ['38'],
 ['39'],
 ['40'],
 ['41'],
 ['42'],
 ['43'],
 ['44'],
 ['45'],
 ['46'],
 ['47'],
 ['48'],
 ['49'],
 ['50'],
 ['51'],
 ['52'],
 ['53'],
 ['54'],
 ['55'],
 ['56'],
 ['57'],
 ['58'],
 ['59'],
 ['60'],
 ['61'],
 ['62'],
 ['63'],
 ['64'],
 ['65'],
 ['66'],
 ['67'],
 ['68'],
 ['69'],
 ['70'],
 ['71'],
 ['72'],
 ['73'],
 ['74'],
 ['75'],
 ['76'],
 ['77'],
 ['78'],
 ['79'],
 ['80'],
 ['81'],
 ['82'],
 ['83'],
 ['84'],
 ['85'],
 ['86'],
 ['87'],
 ['88'],
 ['89'],
 ['90'],
 ['91'],
 ['92'],
 ['93'],
 ['94'],
 ['95'],
 ['96'],
 ['97'],
 ['98'],
 ['99'],
 ['100'],
 ['101'],
 ['102'],
 ['103'],
 ['104'],
 ['105'],
 ['106'],
 ['107'],
 ['108'],
 ['109'],
 ['110'],


# Create a List of Samples

In [46]:
#print(samples)

#vectorSamples = []
#for sentence in samples:
    #accumulatedVector = np.zeros(100)
    #count =0
    #for word in sentence:
        #acumulatedVector = model.wv[word] + accumulatedVector  
        #count=count+1
    
    #vectorSamples.append(acumulatedVector/count)
    
vectorSamples = [] 

for eachString in samplesSingleList:
    vectorSamples.append(model.infer_vector(eachString))
    

# Split the Data

In [47]:
samples_train, samples_test, labels_train, labels_test = train_test_split(
    vectorSamples, labels, test_size=0.33, random_state=42)


labels_train

samples_test

labels_test

samples_train


[array([-3.39184904e+00,  3.16356599e-01, -3.21589351e-01,  1.97120273e+00,
         1.35543942e+00, -3.27681136e+00,  2.16628432e+00, -1.72344244e+00,
        -4.03485250e+00,  9.80170608e-01,  7.30926037e-01,  2.99180317e+00,
         1.67342401e+00,  5.00249267e-01,  2.15601468e+00,  1.97035909e+00,
         3.60566348e-01, -9.77321923e-01, -2.88951218e-01,  3.93817544e-01,
         1.93056631e+00, -1.35750115e+00, -8.06519091e-01, -2.70802200e-01,
         7.61078358e-01,  2.66000368e-02, -6.28769040e-01,  2.73630595e+00,
         2.55202436e+00,  1.75842345e-01, -2.18070459e+00,  4.79484886e-01,
        -6.13337457e-01, -5.46528280e-01, -3.99241209e-01,  2.77128935e+00,
         4.85537082e-01,  1.00379598e+00,  2.00333881e+00,  6.49256289e-01,
         9.99610126e-01, -1.74979225e-01, -1.18812986e-01, -8.79550219e-01,
         1.93990886e-01, -2.29937720e+00, -1.78068626e+00, -9.91783813e-02,
         7.09508240e-01, -9.25525129e-01, -1.14271224e+00, -1.72629440e+00,
        -2.3

# Create the Machine Learning Algorithms

In [48]:
svm_classifier = svm.SVC(kernel='linear',class_weight='balanced')


dt_classifier = tree.DecisionTreeClassifier(class_weight='balanced')


rf_classifier = RandomForestClassifier(n_estimators=10,class_weight='balanced')


nn_classifier = MLPClassifier(hidden_layer_sizes=(100,70),max_iter=500)



# Scoring with vectorSamples and labels

In [49]:
svm_scores = cross_val_score(svm_classifier, vectorSamples, labels, cv=5)
print('SVM scores: ' + str(svm_scores))
svm_average = sum(svm_scores)/5
print('SVM scores average: ' + str(svm_average))

dt_scores = cross_val_score(dt_classifier, vectorSamples, labels, cv=5)
print('DT scores:  ' + str(dt_scores))
dt_average = sum(dt_scores)/5
print('DT scores average: ' + str(dt_average))

rf_scores = cross_val_score(rf_classifier, vectorSamples, labels, cv=5)
print('RF scores:  ' + str(rf_scores))
rf_average = sum(rf_scores)/5
print('RF scores average: ' + str(rf_average))


nn_scores = cross_val_score(nn_classifier, vectorSamples, labels, cv=5)
print('NN scores:  ' + str(nn_scores))
nn_average = sum(nn_scores)/5
print('NN scores average: ' + str(nn_average))

SVM scores: [0.63144654 0.63984674 0.62596401 0.63612565 0.64464993]
SVM scores average: 0.6356065765716724
DT scores:  [0.27169811 0.26564496 0.3033419  0.28141361 0.29590489]
DT scores average: 0.28360069422028156
RF scores:  [0.37358491 0.37675607 0.35475578 0.37172775 0.37912814]
RF scores average: 0.37119052844176487
NN scores:  [0.59874214 0.63090677 0.62467866 0.63219895 0.63011889]
NN scores average: 0.623329082735582


# Scoring with samples_test and labels_test

In [50]:
svm_scores = cross_val_score(svm_classifier, samples_test, labels_test, cv=5)
print('SVM scores: ' + str(svm_scores))
svm_average = sum(svm_scores)/5
print('SVM scores average: ' + str(svm_average))

dt_scores = cross_val_score(dt_classifier, samples_test, labels_test, cv=5)
print('DT scores:  ' + str(dt_scores))
dt_average = sum(dt_scores)/5
print('DT scores average: ' + str(dt_average))

rf_scores = cross_val_score(rf_classifier, samples_test, labels_test, cv=5)
print('RF scores:  ' + str(rf_scores))
rf_average = sum(rf_scores)/5
print('RF scores average: ' + str(rf_average))

nn_scores = cross_val_score(nn_classifier, samples_test, labels_test, cv=5)
print('NN scores:  ' + str(nn_scores))
nn_average = sum(nn_scores)/5
print('NN scores average: ' + str(nn_average))

/home/hraval/.conda/envs/local/lib/python3.6/site-packages/sklearn/model_selection/_split.py:605: Warning: The least populated class in y has only 4 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)


SVM scores: [0.55797101 0.58646617 0.55598456 0.58130081 0.56652361]
SVM scores average: 0.5696492308098376


/home/hraval/.conda/envs/local/lib/python3.6/site-packages/sklearn/model_selection/_split.py:605: Warning: The least populated class in y has only 4 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)


DT scores:  [0.2173913  0.19548872 0.22393822 0.20731707 0.20600858]
DT scores average: 0.210028781390456


/home/hraval/.conda/envs/local/lib/python3.6/site-packages/sklearn/model_selection/_split.py:605: Warning: The least populated class in y has only 4 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)


RF scores:  [0.27173913 0.29699248 0.29343629 0.27642276 0.35193133]
RF scores average: 0.2981043999547658


/home/hraval/.conda/envs/local/lib/python3.6/site-packages/sklearn/model_selection/_split.py:605: Warning: The least populated class in y has only 4 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)


NN scores:  [0.36956522 0.51503759 0.46718147 0.50406504 0.53648069]
NN scores average: 0.4784660011806839


# Fit the Model

In [51]:
svm_classifier = svm.SVC(kernel='linear',class_weight='balanced')


dt_classifier = tree.DecisionTreeClassifier(class_weight='balanced')


rf_classifier = RandomForestClassifier(n_estimators=10,class_weight='balanced')


nn_classifier = MLPClassifier(hidden_layer_sizes=(100,70),max_iter=500)

svm_classifier.fit(samples_train,labels_train)
dt_classifier.fit(samples_train,labels_train)
rf_classifier.fit(samples_train,labels_train)
nn_classifier.fit(samples_train,labels_train)

MLPClassifier(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
       beta_2=0.999, early_stopping=False, epsilon=1e-08,
       hidden_layer_sizes=(100, 70), learning_rate='constant',
       learning_rate_init=0.001, max_iter=500, momentum=0.9,
       nesterovs_momentum=True, power_t=0.5, random_state=None,
       shuffle=True, solver='adam', tol=0.0001, validation_fraction=0.1,
       verbose=False, warm_start=False)

# Final Scores

In [52]:
score = svm_classifier.score(samples_test, labels_test)
print('SVM score: ' + str(score))
score = dt_classifier.score(samples_test, labels_test)
print('DT score: ' + str(score))
score = rf_classifier.score(samples_test, labels_test)
print('RF score: ' + str(score))
score = nn_classifier.score(samples_test, labels_test)
print('NN score: ' + str(score))

SVM score: 0.6140625
DT score: 0.265625
RF score: 0.37265625
NN score: 0.61796875
